In [2]:
import os
from groq import Groq
import pandas as pd
import numpy as np

In [3]:
apiKey = "fill_it_here"

In [4]:
client = Groq(
    # api_key=os.environ.get("GROQ_API_KEY"),
    api_key= apiKey,
)

In [5]:
dataset = pd.read_csv("/home/patrick/Downloads/test3label/keyphrases/done/keyphrases_AmazonMixtral_Done.csv")

In [6]:
dataset

Unnamed: 0                                            content  \
0              0  Thank you for giving me the chance to build up...   
1            939  Buggy as all get out these days. I have not be...   
2           1720  Did not do a lot for me I need more than that ...   
3           2132  Yes, satisfied, but, the throw I bought was to...   
4           2209  I just got on the app about a month ago and I ...   
...          ...                                                ...   
2695        2620  When I use search and type in for example Elec...   
2696        2623  Freezes. Stalls. Overheats CPU. Battery hog. U...   
2697        2631  Pathetic customer care. Supplied wrong deliver...   
2698        2662  I don't like Amazon anymore because they are s...   
2699        2695  App keeps crashing since last update, app free...   

                                    keyphrases_original  cluster  sentiment  \
0     ['building credit rating', '0 dollars owed', '...      343          2   
1     ['Buggy app', 'user experience issues', 'past ...      343          1   
2     ['Did not do a lot', 'user experience', 'need ...      343          2   
3     ['user satisfaction', 'purchased item too narr...      343          1   
4     ['enjoying Amazon App', 'used for a month', 'n...      343          2   
...                                                 ...      ...        ...   
2695  ['user experience', 'search function', 'Electr...      373          2   
2696  ['Freezes', 'Stalls', 'Overheats CPU', 'Batter...      344          0   
2697  ['Pathetic customer care', 'wrong delivered it...      426          0   
2698  ['user comment about Amazon App', 'dislike for...      383          0   
2699  ['app keeps crashing', 'last update issue', 'a...      371          0   

      count                                 keyphrases_reduced  \
0         6  ['Amazon App usage', 'credit rating improvemen...   
1         6  ['Amazon App usage', 'credit rating improvemen...   
2         6  ['Amazon App usage', 'credit rating improvemen...   
3         6  ['Amazon App usage', 'credit rating improvemen...   
4         6  ['Amazon App usage', 'credit rating improvemen...   
...     ...                                                ...   
2695      1  ['user experience', 'search function', 'Electr...   
2696      1  ['Freezes', 'Stalls', 'Overheats CPU', 'Batter...   
2697      1  ['Pathetic customer care', 'wrong delivered it...   
2698      1  ['user comment about Amazon App', 'dislike for...   
2699      1  ['app keeps crashing', 'last update issue', 'a...   

                              Merged keyphrases_reduced  \
0     ['Amazon App usage', 'credit rating improvemen...   
1     ['Amazon App usage', 'credit rating improvemen...   
2     ['Amazon App usage', 'credit rating improvemen...   
3     ['Amazon App usage', 'credit rating improvemen...   
4     ['Amazon App usage', 'credit rating improvemen...   
...                                                 ...   
2695  ['using Amazon App', 'shopping experience', 'u...   
2696  ['Freezes', 'Stalls', 'Overheats CPU', 'Batter...   
2697  ['user comment', 'Amazon App issue', 'complain...   
2698  ['using Amazon App', 'shopping experience', 'u...   
2699  ['user comment', 'Amazon App issue', 'complain...   

      count merged keyphrases_reduced kw newly generated  id Mkr  \
0                                   6                NaN       0   
1                                   6                NaN       0   
2                                   6                NaN       0   
3                                   6                NaN       0   
4                                   6                NaN       0   
...                               ...                ...     ...   
2695                               10               True     406   
2696                                1                NaN     420   
2697                               10               True     404   
2698                  

In [7]:
score_counts_balanced = dataset['sentiment'].value_counts().sort_index()
print(score_counts_balanced)

sentiment
0    900
1    900
2    900
Name: count, dtype: int64


In [8]:
train_data = dataset[['content', 'sentiment', 'Merged keyphrases_reduced 2']]
train_data['row_number'] = train_data.index

/tmp/ipykernel_2744438/1289041381.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_data['row_number'] = train_data.index


In [9]:
train_data

content  sentiment  \
0     Thank you for giving me the chance to build up...          2   
1     Buggy as all get out these days. I have not be...          1   
2     Did not do a lot for me I need more than that ...          2   
3     Yes, satisfied, but, the throw I bought was to...          1   
4     I just got on the app about a month ago and I ...          2   
...                                                 ...        ...   
2695  When I use search and type in for example Elec...          2   
2696  Freezes. Stalls. Overheats CPU. Battery hog. U...          0   
2697  Pathetic customer care. Supplied wrong deliver...          0   
2698  I don't like Amazon anymore because they are s...          0   
2699  App keeps crashing since last update, app free...          0   

                            Merged keyphrases_reduced 2  row_number  
0     ['Amazon App usage', 'credit rating improvemen...           0  
1     ['Amazon App usage', 'credit rating improvemen...           1  
2     ['Amazon App usage', 'credit rating improvemen...           2  
3     ['Amazon App usage', 'credit rating improvemen...           3  
4     ['Amazon App usage', 'credit rating improvemen...           4  
...                                                 ...         ...  
2695  ["Amazon App", "User Experience", "Shopping", ...        2695  
2696  ['Freezes', 'Stalls', 'Overheats CPU', 'Batter...        2696  
2697  ['User Sentiment', 'Amazon', 'User Experience ...        2697  
2698  ["Amazon App", "User Experience", "Shopping", ...        2698  
2699  ['User Sentiment', 'Amazon', 'User Experience ...        2699  

[2700 rows x 4 columns]

In [10]:
list = []
i = 0
for index, row in train_data.iterrows():
    text = row['content']
    topics = row['Merged keyphrases_reduced 2']
    string_message = f"""I need you to evaluate and assess the comment along with the set of topics/keyphrases, categorizing their sentiment into one of five levels: 1 - negative, 2 - neutral, or 3 - positive. Here are examples to guide your classification:

                1. Comment: "Latest update (last week) is the worst of all. App crashes every other search now. When it does work is slow to load."
                Topics / Keyphrases: ["User Experience", "Shopping", "Item Returns", "Country Change", "Prime Membership", "Payment Issues", "Location Settings", "Delivery Speed Comparison", "Design Issue", "User Sentiment"]
                Label: 1
                
                2. Comment: "Boycotting American companies. US Gov has blood on its hands."
                Topics / Keyphrases: ['boycotting American companies', 'US Gov blood on its hands', 'Google Play Store controversies', 'Amazon App allegations', 'negative user sentiment', 'political statements in user comments', 'baseless censorship', 'user experience and content moderation', 'fraudulent incidents and app security', 'unauthorized charges and data protection']
                Label: 1
                
                3. Comment: "Ever since the new update the app won't stop crashing. "app isn't responding""
                Topics / Keyphrases: ['Amazon App problems', 'app crashing', 'app unresponsiveness', 'mobile application issues', 'update issues', 'order tracking failure', 'video interference', 'user experience issues', 'app stability', 'technical difficulties']
                Label: 1                
                
                4. Comment: "First there was the update that dropped the search bar to the bottom of the screen. Now this update puts all my orders in chronological order, instead of organizing by delivery date. One of my items on backorder is buried now and I have to scroll through to find it. Why are you changing things that have been standard on the app? Who is making these decisions? Do you even consult with focus groups?"
                Topics / Keyphrases: ['new update search bar', 'bottom screen placement', 'orders chronological organization', 'delivery date sorting', 'backordered item visibility', 'efficient item location', 'app decision-making features', 'focus group feedback', 'user experience complaints', 'feature toggle location']
                Label: 1
                
                5. Comment: "Amazon used to be a lot better. Now I can't even disable certain notifications without disabling them all, including delivery notifications. Furthermore if you disable them they will stop donating through Amazon smile. And in the last few years I have gotten double the broken deliveries, wrong deliveries, stuff missing due to misdeliveries, expired or miscounted food items, late deliveries, randomly canceled deliveries, and just about every other annoying thing you can imagine for online orders."
                Topics / Keyphrases: ['Amazon App notifications', 'scummy tactic forcing ads', 'excess email spams', 'difficult to opt-out', 'app changing issues', 'white interface burning retinas', 'delivery issues', 'shady marketing notifications', 'preference for old app version', 'considering to uninstall']
                Label: 1
                
                6. Comment: "Wish shipping was faster for my area but I love the app and prices I will continue to order and keep ordering"
                Topics / Keyphrases: ['user comment', 'Google Play Store', 'Amazon App', 'slow app', 'app speed', 'product prices', 'wish shipping was faster', 'specific area', 'not buying', 'years', 'user experience', 'likes the app', 'continues to order', 'jeff bezos', 'taken over', 'will consider buying', 'prices', 'keeps ordering', 'analysis']
                Label: 2
                
                7. Comment: "Worked fine until i updated the app, now doesnt work at All."
                Topics / Keyphrases: ['Matt Edmon', 'user comment', 'Google Play Store', 'Amazon App', 'version', 'undownloading itself', 'data loss', 'item searching', 'functionality issues', 'data security']
                Label: 2
                                
                8. Comment: "Edit: I haven't seen ads recently so I'm giving a couple stars back......... They put adverstisements in the main notification channel so there's no way to mute ad notifications without losing all notifications. Pretty scummy tactic to force users into ads"
                Topics / Keyphrases: ['Amazon App notifications', 'scummy tactic forcing ads', 'excess email spams', 'difficult to opt-out', 'app changing issues', 'white interface burning retinas', 'delivery issues', 'shady marketing notifications', 'preference for old app version', 'considering to uninstall']
                Label: 2
                                                
                9. Comment: "Delivery is always on point and this app is great, but my only issue is that the screen keeps on freezing, I can barely use it. Overall, nice job."
                Topics / Keyphrases: ["User Experience", "Shopping", "Item Returns", "Country Change", "Prime Membership", "Payment Issues", "Location Settings", "Delivery Speed Comparison", "Design Issue", "User Sentiment"]
                Label: 2                
                
                10. Comment: "Can the app be renamed to just Amazon on Android?"
                Topics / Keyphrases: ['Amazon App integration', 'Android device issues', 'User suggestion for app name change', 'App title and user experience', 'Play Store comments on Amazon App', 'Intrusive advertisements', 'App restrictions and OS compatibility', 'Context menu takeover and accessibility', 'Notification settings privacy concerns', 'Amazon App language options and localization']
                Label: 2

                11. Comment: "It's very good to be able to have amazon on my phone again"
                Topics / Keyphrases: ['Amazon app', 'user experience', 'senior & handicapped accessibility', 'user convenience', 'e-commerce platform', 'shopping efficiency', 'affordable purchases', 'app performance', 'reliable source for daily needs', 'Amazon Prime benefits']
                Label: 3

                12. Comment: "Amazon is pretty damn good I don't have nothing to say about it"
                Topics / Keyphrases: ['Amazon app user experience', 'Google Play Store user comments', 'E-commerce platform evaluation', 'Ads in Amazon app', 'First-party ads concerns', 'Gift options and privacy', 'Assistance for limited mobility', 'App functionality and order delivery', 'Product affordability and availability', 'Digital marketplace user feedback']
                Label: 3
                
                13. Comment: "Great with prime and customer support always help with issues"
                Topics / Keyphrases: ['Amazon App', 'compatible with Prime', 'customer support', 'issues resolution', 'user experience', 'language support', 'app updates', 'split payment feature', 'app functionality', 'app customization']
                Label: 3
                
                14. Comment: "Love amazon, but could you add an option to your app so that we can make it dark theme?"
                Topics / Keyphrases: ['Amazon App user interface request', 'Dark mode option', 'User experience themes', 'Accessibility and visual preference', 'Google Play Store user feedback', 'User comments on appearance', 'Remove from cart feature request', 'Amazon App customization', 'Voice search alternative', 'Virtual assistant user experience']
                Label: 3
                
                15. Comment: "Fastest and satifier shopping app for me and you."
                Topics / Keyphrases: ['Amazon App user experience', 'Purchasing from Amazon App', 'App functionality', 'User comments on Google Play Store', 'Comment analysis', 'Florsheim shoe selection', 'Digital content purchase', 'Order management', 'Invoice printing', 'App localization']
                Label: 3

                
                Please provide the sentiment classification as a single number (1, 2, or 3) and nothing more for the following comment:

                Comment: "{text}"
                Topics / Keyphrases: {topics}
                Label: ?
                """
    print("\n\n")
    print(string_message)
    print("\n")
    
    chat_completion = client.chat.completions.create(
        messages = [
            {
                "role": "user",
                "content": f"""{string_message}"""
            }
    
        ],
        # model="llama3-8b-8192",
        model="mixtral-8x7b-32768",
    )
    
    armaz = chat_completion.choices[0].message.content
    print(f'{index}:\t{armaz}')
    list.append(armaz)




I need you to evaluate and assess the comment along with the set of topics/keyphrases, categorizing their sentiment into one of five levels: 1 - negative, 2 - neutral, or 3 - positive. Here are examples to guide your classification:

                1. Comment: "Latest update (last week) is the worst of all. App crashes every other search now. When it does work is slow to load."
                Topics / Keyphrases: ["User Experience", "Shopping", "Item Returns", "Country Change", "Prime Membership", "Payment Issues", "Location Settings", "Delivery Speed Comparison", "Design Issue", "User Sentiment"]
                Label: 1
                
                2. Comment: "Boycotting American companies. US Gov has blood on its hands."
                Topics / Keyphrases: ['boycotting American companies', 'US Gov blood on its hands', 'Google Play Store controversies', 'Amazon App allegations', 'negative user sentiment', 'political statements in user comments', 'baseless censorship', 'use

In [ ]:
len(list)

192

In [13]:
rest = train_data[len(list):]
for index, row in rest.iterrows():
    text = row['content']
    topics = row['Merged keyphrases_reduced 2']
    string_message = f"""I need you to evaluate and assess the comment along with the set of topics/keyphrases, categorizing their sentiment into one of five levels: 1 - negative, 2 - neutral, or 3 - positive. Here are examples to guide your classification:

                1. Comment: "Latest update (last week) is the worst of all. App crashes every other search now. When it does work is slow to load."
                Topics / Keyphrases: ['Amazon App issue', 'Update problems', 'App crashing', 'Functionality problems', 'Performance issues', 'Software bugs', 'App malfunction', 'Update failure', 'Crashing issue', 'App update issues']
                Label: 1
                
                2. Comment: "Boycotting American companies. US Gov has blood on its hands."
                Topics / Keyphrases: ['Amazon Boycott', 'Censorship Concerns', 'Genocide Support Criticism', 'Company Ethics Issues', 'Free Speech Algorithm', 'Human Rights Violation', 'Economic Political Disapproval', 'Controversial Brand Image', 'App Controversy Protest', 'Ethical Business Practices']
                Label: 1
                
                3. Comment: "Ever since the new update the app won't stop crashing. "app isn't responding""
                Topics / Keyphrases: ['Amazon App crashes', 'Crashing issues', 'App performance problems', 'Update problems', 'Error messages', 'Technical issues', 'App not responding', 'Slow search', 'Search engine issues', 'App freezes']
                Label: 1                
                
                4. Comment: "First there was the update that dropped the search bar to the bottom of the screen. Now this update puts all my orders in chronological order, instead of organizing by delivery date. One of my items on backorder is buried now and I have to scroll through to find it. Why are you changing things that have been standard on the app? Who is making these decisions? Do you even consult with focus groups?"
                Topics / Keyphrases: ['Amazon app improvement', 'User interface overhaul', 'Order organization and tracking', 'Search functionality enhancement', 'Notification management', 'Delivery instructions and options', 'App design and performance', 'Customer feedback and experience', 'Order history and management', 'Notification and alert system improvement']
                Label: 1
                
                5. Comment: "Amazon used to be a lot better. Now I can't even disable certain notifications without disabling them all, including delivery notifications. Furthermore if you disable them they will stop donating through Amazon smile. And in the last few years I have gotten double the broken deliveries, wrong deliveries, stuff missing due to misdeliveries, expired or miscounted food items, late deliveries, randomly canceled deliveries, and just about every other annoying thing you can imagine for online orders."
                Topics / Keyphrases: ['Amazon App issues and problems', 'Cart and order management struggles', 'Package tracking and delivery glitches', 'Amazon account and login errors', 'Unreliable and inaccurate order tracking', 'Shopping app experience issues', 'cart and order retrieval difficulties', 'Amazon Fresh and delivery problems', 'Notification and package delivery issues', 'Order and delivery accuracy concerns']
                Label: 1
                
                6. Comment: "Wish shipping was faster for my area but I love the app and prices I will continue to order and keep ordering"
                Topics / Keyphrases: ['Amazon App User Experience', 'Credit Score Improvement', 'Shipping Speed and Satisfaction', 'First Impression and Feedback', 'Convenience and Features', 'New User Initial Experience', 'App Store Availability and Reinstatement', 'Credit History and Purchasing Habits', 'User Expectations and Satisfaction', 'App Update and Improvement']
                Label: 2
                
                7. Comment: "Worked fine until i updated the app, now doesnt work at All."
                Topics / Keyphrases: ['Amazon App issue', 'Update problems', 'App crashing', 'Functionality problems', 'Performance issues', 'Software bugs', 'App malfunction', 'Update failure', 'Crashing issue', 'App update issues']
                Label: 2
                                
                8. Comment: "Edit: I haven't seen ads recently so I'm giving a couple stars back......... They put adverstisements in the main notification channel so there's no way to mute ad notifications without losing all notifications. Pretty scummy tactic to force users into ads"
                Topics / Keyphrases: ['Amazon App issues with account creation and login', 'Disturbing ads experience', 'Digital rewards and product authenticity concerns', 'Amazon shopping experience problems with notification and ad issues', 'App freezes and crashes with searching and browsing issues', 'Hacked Prime Account issues with security and verification', 'Amazon app malfunction with sign up and registration issues', 'Customer service complaint with lack of human support and UX problems', 'App performance issues with blank white screen and error behavior', 'Order access and retrieval issues with account and language flags']
                Label: 2
                                                
                9. Comment: "Delivery is always on point and this app is great, but my only issue is that the screen keeps on freezing, I can barely use it. Overall, nice job."
                Topics / Keyphrases: ['Amazon app issues', 'poor performance', 'screen freezing', 'user experience', 'positive review', 'good features', 'customer satisfaction', 'app functionality', 'purchase satisfaction', 'software quality']
                Label: 2                
                
                10. Comment: "Can the app be renamed to just Amazon on Android?"
                Topics / Keyphrases: ['Amazon App Rename Options', 'Dark Mode User Feedback', 'Slow App Performance Fix', 'User-Centric App Customization', 'Search Functionality Improvement', '4G Network App Speed Boost', 'Mobile App User Experience Enhancement', 'Google Play Store Amazon App', 'Customizable User Interface', 'Alexa Voice Search Integration']
                Label: 2

                11. Comment: "It's very good to be able to have amazon on my phone again"
                Topics / Keyphrases: ['Amazon App User Experience', 'Credit Score Improvement', 'Shipping Speed and Satisfaction', 'First Impression and Feedback', 'Convenience and Features', 'New User Initial Experience', 'App Store Availability and Reinstatement', 'Credit History and Purchasing Habits', 'User Expectations and Satisfaction', 'App Update and Improvement']
                Label: 3

                12. Comment: "Amazon is pretty damn good I don't have nothing to say about it"
                Topics / Keyphrases: ['Amazon app issues', 'poor performance', 'screen freezing', 'user experience', 'positive review', 'good features', 'customer satisfaction', 'app functionality', 'purchase satisfaction', 'software quality']
                Label: 3
                
                13. Comment: "Great with prime and customer support always help with issues"
                Topics / Keyphrases: ['Amazon user experience', 'Positive experience with Amazon', 'Amazon app performance', 'Customer support with Amazon', 'Good shopping experience on Amazon', 'Effective issue resolution', 'Amazon service quality', 'Prime benefits and perks', 'Satisfying purchase experience on Amazon', 'Reliable online shopping experience with Amazon']
                Label: 3
                
                14. Comment: "Love amazon, but could you add an option to your app so that we can make it dark theme?"
                Topics / Keyphrases: ['Amazon App Rename Options', 'Dark Mode User Feedback', 'Slow App Performance Fix', 'User-Centric App Customization', 'Search Functionality Improvement', '4G Network App Speed Boost', 'Mobile App User Experience Enhancement', 'Google Play Store Amazon App', 'Customizable User Interface', 'Alexa Voice Search Integration']
                Label: 3
                
                15. Comment: "Fastest and satifier shopping app for me and you."
                Topics / Keyphrases: ['Amazing Shopping Experience', 'Fast and Satisfying App', 'Easy Online Shopping', 'High Quality Items', 'Good Product Variety', 'Fast and Reliable Delivery', 'User Friendly App', 'Secure Online Transactions', 'Positive Customer Reviews', 'Convenient E-commerce Platform']
                Label: 3

                
                Please provide the sentiment classification as a single number (1, 2, or 3) and nothing more for the following comment:

                Comment: "{text}"
                Topics / Keyphrases: {topics}
                Label: ?
                """
    print("\n\n")
    print(string_message)
    print("\n")
    
    chat_completion = client.chat.completions.create(
        messages = [
            {
                "role": "user",
                "content": f"""{string_message}"""
            }
    
        ],
        # model="llama3-8b-8192",
        model="mixtral-8x7b-32768",
    )
    
    armaz = chat_completion.choices[0].message.content
    print(f'{index}:\t{armaz}')
    list.append(armaz)




I need you to evaluate and assess the comment along with the set of topics/keyphrases, categorizing their sentiment into one of five levels: 1 - negative, 2 - neutral, or 3 - positive. Here are examples to guide your classification:

                1. Comment: "Latest update (last week) is the worst of all. App crashes every other search now. When it does work is slow to load."
                Topics / Keyphrases: ['Amazon App issue', 'Update problems', 'App crashing', 'Functionality problems', 'Performance issues', 'Software bugs', 'App malfunction', 'Update failure', 'Crashing issue', 'App update issues']
                Label: 1
                
                2. Comment: "Boycotting American companies. US Gov has blood on its hands."
                Topics / Keyphrases: ['Amazon Boycott', 'Censorship Concerns', 'Genocide Support Criticism', 'Company Ethics Issues', 'Free Speech Algorithm', 'Human Rights Violation', 'Economic Political Disapproval', 'Controversial Brand Image',

In [ ]:
len(list)

In [ ]:
# list.pop()

In [ ]:
list

In [ ]:
train_data['predictedSentiment'] = pd.Series(list)

In [ ]:
train_data

In [35]:
import re

def contains_number(s):
    return any(char.isdigit() for char in s)

def findNumbers(string):
    # Find all numbers in the string
    numbers = None
    if(contains_number(string)):
        numbers = re.findall(r'\d+', string)
    else:
        numbers = ""
    
    # Convert the numbers to integers
    
    numbers = [int(x) for x in numbers]
    
    if(len(numbers)>0):
        x = numbers[0]-1
    else:
        x = -1
    return x

In [36]:
formated = train_data['predictedSentiment'].apply(findNumbers)

In [ ]:
train_data['predictedSentiment'] = formated

In [ ]:
train_data

In [39]:
train_data.to_csv('/home/patrick/Downloads/test3label/mixtralOutput/topics/filenameAmazonFewShotMixtral-T.csv', index=False)

In [106]:
results = pd.read_csv("/home/patrick/Downloads/test3label/mixtralOutput/topics/filenameAmazonFewShotMixtral-T.csv")

In [ ]:
results

In [ ]:
results['predictedSentiment'].value_counts().sort_index()

In [109]:
filtered_df = results[results["predictedSentiment"] == -1]

In [ ]:
filtered_df

In [111]:
newResults = results[results["predictedSentiment"] != -1]

In [ ]:
newResults

In [113]:
from matplotlib.ticker import PercentFormatter
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.metrics import confusion_matrix

def cm_analysis(y_true, y_pred, filename, labels, classes, ymap=None, figsize=(17,17)):
    """
    Generate matrix plot of confusion matrix with pretty annotations.
    The plot image is saved to disk.
    args: 
      y_true:    true label of the data, with shape (nsamples,)
      y_pred:    prediction of the data, with shape (nsamples,)
      filename:  filename of figure file to save
      labels:    string array, name the order of class labels in the confusion matrix.
                 use `clf.classes_` if using scikit-learn models.
                 with shape (nclass,).
      classes:   aliases for the labels. String array to be shown in the cm plot.
      ymap:      dict: any -> string, length == nclass.
                 if not None, map the labels & ys to more understandable strings.
                 Caution: original y_true, y_pred and labels must align.
      figsize:   the size of the figure plotted.
    """
    sns.set(font_scale=2.8)

    if ymap is not None:
        y_pred = [ymap[yi] for yi in y_pred]
        y_true = [ymap[yi] for yi in y_true]
        labels = [ymap[yi] for yi in labels]
    cm = confusion_matrix(y_true, y_pred, labels=labels)
    cm_sum = np.sum(cm, axis=1, keepdims=True)
    cm_perc = cm / cm_sum.astype(float) * 100
    annot = np.empty_like(cm).astype(str)
    nrows, ncols = cm.shape
    for i in range(nrows):
        for j in range(ncols):
            c = cm[i, j]
            p = cm_perc[i, j]
            if i == j:
                s = cm_sum[i]
                annot[i, j] = '%.2f%%\n%d/%d' % (p, c, s)
            #elif c == 0:
            #    annot[i, j] = ''
            else:
                annot[i, j] = '%.2f%%\n%d' % (p, c)
    cm = confusion_matrix(y_true, y_pred, labels=labels, normalize='true')
    cm = pd.DataFrame(cm, index=labels, columns=labels)
    cm = cm * 100
    cm.index.name = 'True Label'
    cm.columns.name = 'Predicted Label'
    fig, ax = plt.subplots(figsize=figsize)
    plt.yticks(va='center')

    sns.heatmap(cm, annot=annot, fmt='', ax=ax, xticklabels=classes, cbar=True, cbar_kws={'format':PercentFormatter()}, yticklabels=classes, cmap="Blues")
    plt.savefig(f'{filename}.png',  bbox_inches='tight')
    plt.savefig(f'{filename}.svg',  bbox_inches='tight')

In [114]:
# Generate the confusion matrix
unique_labels = np.sort(newResults['scoreSA'].unique())
mapping = {0: 'Very Negative (1)', 1: 'Negative (2)', 2: 'Neutral (3)', 3: 'Positive (4)', 4: 'Very Positive (5)'}

# Applying mapping
classes = [mapping[value] for value in unique_labels]

In [ ]:
cm_analysis(newResults['scoreSA'], newResults['predictedSentiment'], 'API', unique_labels, classes)

In [116]:
from sklearn.metrics import accuracy_score, balanced_accuracy_score, precision_score, recall_score, f1_score, precision_recall_fscore_support, mean_absolute_error

accuracy = accuracy_score(newResults['scoreSA'], newResults['predictedSentiment'])
precision_ALL = precision_score(newResults['scoreSA'], newResults['predictedSentiment'], average='macro')
recall_ALL = recall_score(newResults['scoreSA'], newResults['predictedSentiment'], average='macro')
f1_ALL = f1_score(newResults['scoreSA'], newResults['predictedSentiment'], average='macro')
mae_ALL = mean_absolute_error(newResults['scoreSA'], newResults['predictedSentiment'])
precision, recall, f1, support = precision_recall_fscore_support(newResults['scoreSA'], newResults['predictedSentiment'])

In [ ]:
# Calculate accuracy for each class
for i in range(len(unique_labels)):
    temp = newResults[newResults["scoreSA"] == i]
    value = accuracy_score(temp['scoreSA'], temp['predictedSentiment'])
    print(f'Label:\t{i}\t-\tValue:\t{value}')

In [ ]:
accuracy

In [ ]:
balanced_accuracy = balanced_accuracy_score(results['scoreSA'], results['predictedSentiment'])

In [ ]:
balanced_accuracy

In [ ]:
precision_ALL

In [ ]:
f1_ALL

In [ ]:
recall_ALL

In [ ]:
mae_ALL

In [ ]:
f1

In [ ]:
precision

In [ ]:
recall

In [ ]:
support